# Пайплайн № 4
### База знаний: FAQ и Реальные Кейсы

### Защита от галлюцинаций: если не уверены в ответе - возвращаем "Нет ответа", но отдаём два классификатора.

### Установка необходимых библиотек

In [20]:
%%bash

pip install haystack-ai
pip install "datasets>=2.6.1"
pip install "sentence-transformers>=3.0.0"
pip install pymorphy2
pip install catboost

### Подготовка данных

In [21]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [22]:
!cp -r drive/MyDrive/HacksAI/Russia24/Dataset Dataset/

Эталонная База Знаний FAQ

In [23]:
import pandas as pd
import json

know_base_path = 'Dataset/01_База_знаний.xlsx'
df_base = pd.read_excel(know_base_path)

df_base.head()

Тема  \
0                   Что нельзя публиковать на RUTUBE   
1  Почему могут отключить монетизацию на видео и ...   
2  Почему могут отключить монетизацию на видео и ...   
3  Почему могут отключить монетизацию на видео и ...   
4                                    Авторское право   

                                        Вопрос из БЗ  \
0                  Что нельзя публиковать на RUTUBE?   
1  Почему могут отключить монетизацию из-за автор...   
2  Почему могут отключить монетизацию из-за искус...   
3  Для каких статусов доступна монетизация, и поч...   
4  Какой контент можно использовать для монетизац...   

                                         Ответ из БЗ Классификатор 1 уровня  \
0  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
1  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
2  Монетизация на RUTUBE зависит в том числе от к...            МОНЕТИЗАЦИЯ   
3  Монетизацию на RUTUBE можно подключить, если в...            МОНЕТИЗАЦИЯ   
4  То, что вы создали сами: видео, которое вы сня...            МОНЕТИЗАЦИЯ   

               Классификатор 2 уровня  
0         Отклонение/блокировка видео  
1  Отключение/подключение монетизации  
2  Отключение/подключение монетизации  
3  Отключение/подключение монетизации  
4  Отключение/подключение монетизации

База Реальных Кейсов

In [24]:
real_case_path = 'Dataset/02_Реальные_кейсы.xlsx'
df_case = pd.read_excel(real_case_path)

df_case.head()

Вопрос пользователя  \
0  Здравствуйте! Можно уточнить причины Правилhtt...   
1  Добрый вечер, какой топ причин блокировки виде...   
2  Все пишут, что монетизация на рутубе отключает...   
3  Что запрещено в монетизации и что можно выклад...   
4  Чтобы не отключали монетизацию, надо, чтобы я ...   

                                    Ответ сотрудника  \
0  Добрый день!\nЧто нельзя публиковать на RUTUBE...   
1  Добрый вечер!\nЧто заперщено публиковать на RU...   
2  Добрый день! \nМонетизация может отключиться, ...   
3  Здравствуйте!\nМонетизация может отключиться, ...   
4  Для монетизации можно использовать то, что вы ...   

                                        Вопрос из БЗ  \
0                  Что нельзя публиковать на RUTUBE?   
1                  Что нельзя публиковать на RUTUBE?   
2  Почему могут отключить монетизацию из-за автор...   
3  Почему могут отключить монетизацию из-за автор...   
4  Почему могут отключить монетизацию из-за автор...   

                                         Ответ из БЗ Классификатор 1 уровня  \
0  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
1  Чужой контент без разрешения автора или правоо...              МОДЕРАЦИЯ   
2  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
3  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   
4  Монетизация может отключиться, если на вашем к...            МОНЕТИЗАЦИЯ   

               Классификатор 2 уровня  
0         Отклонение/блокировка видео  
1         Отклонение/блокировка видео  
2  Отключение/подключение монетизации  
3  Отключение/подключение монетизации  
4  Отключение/подключение монетизации

Объединим обе базы для полее полного и объективного поиска

In [25]:
combined_column = pd.concat([df_base['Вопрос из БЗ'], df_case['Вопрос пользователя']], ignore_index=True)

df_base_rest = df_base.drop(columns=['Вопрос из БЗ'])
df_case_rest = df_case.drop(columns=['Вопрос пользователя'])

combined_rest = pd.concat([df_base_rest, df_case_rest], ignore_index=True)

final_df = combined_rest.copy()
final_df['Вопрос'] = combined_column

final_df = final_df[['Вопрос'] + [col for col in final_df.columns if col != 'Вопрос']]
final_df = final_df.drop(columns=["Тема"])

final_df.tail()

Вопрос  \
1122  Добрый день! Как добавить таймкоды в видео?   
1123             Как добавить временные интервалы   
1124        В каком формате добавляются таймкоды?   
1125          Как мне правильно указать тайм-код?   
1126     Как правильно указывать время под видео?   

                                            Ответ из БЗ  \
1122  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1123  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1124  Главное — соблюдать несколько правил.\n\nТайм-...   
1125  Главное — соблюдать несколько правил.\n\nТайм-...   
1126  Главное — соблюдать несколько правил.\n\nТайм-...   

     Классификатор 1 уровня Классификатор 2 уровня  \
1122                  ВИДЕО         Загрузка видео   
1123                  ВИДЕО         Загрузка видео   
1124                  ВИДЕО         Загрузка видео   
1125                  ВИДЕО         Загрузка видео   
1126                  ВИДЕО         Загрузка видео   

                                       Ответ сотрудника  \
1122  Характеристики эпизодов:\n\nОпределяются по та...   
1123  Перейдите в раздел «Видео» в Студии RUTUBE.\nН...   
1124  Формат: минуты:секунды или часы:минуты:секунды...   
1125  Можете указать минуты:секунды или часы:минуты:...   
1126  Тайм-код должен отображать время в формате мин...   

                                           Вопрос из БЗ  
1122                  Как добавить тайм-коды под видео?  
1123                  Как добавить тайм-коды под видео?  
1124  В каком формате нужно добавлять тайм-коды под ...  
1125  В каком формате нужно добавлять тайм-коды под ...  
1126  В каком формате нужно добавлять тайм-коды под ...

In [26]:
from datasets import load_dataset
from haystack import Document

docs = [Document(content=row["Вопрос"], meta={"idx": index}) for index, row in final_df.iterrows()]

### Инициализируем Трансформер для построения эмбеддинга вопросов

In [27]:
from haystack.components.embedders import SentenceTransformersDocumentEmbedder
from haystack.utils import ComponentDevice, Device

device = ComponentDevice.from_str("cuda:0")

# embed_model = "cointegrated/LaBSE-en-ru"
embed_model = "intfloat/e5-large-v2"

doc_embedder = SentenceTransformersDocumentEmbedder(
    model=embed_model,
    device=device
    )

doc_embedder.warm_up()

### Запишем вопросы в векторное хранилище

In [28]:
from haystack.document_stores.in_memory import InMemoryDocumentStore

document_store = InMemoryDocumentStore()

docs_with_embeddings = doc_embedder.run(docs)
unique_docs = {doc.id: doc for doc in docs_with_embeddings["documents"]}.values()
document_store.write_documents(list(unique_docs))

Batches:   0%|          | 0/36 [00:00<?, ?it/s]

1127

### Инициализируем Трансформер для поиска по эмбеддингам вопросов
он должен совпадать с трансформером, на основе которого строились эмбеддинги

In [29]:
from haystack.components.embedders import SentenceTransformersTextEmbedder

text_embedder = SentenceTransformersTextEmbedder(
    model=embed_model,
    device=device
)

### Инициализируем Retriever

In [30]:
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever

retriever = InMemoryEmbeddingRetriever(document_store, top_k=10)

## Собираем пайплайн

In [31]:
from haystack import Pipeline

from haystack.components.rankers import TransformersSimilarityRanker

# ranker = TransformersSimilarityRanker(
#     model="DiTy/cross-encoder-russian-msmarco",
#     top_k=1
#     )

basic_rag_pipeline = Pipeline()
# Add components to your pipeline
basic_rag_pipeline.add_component("text_embedder", text_embedder)
basic_rag_pipeline.add_component("retriever", retriever)
# basic_rag_pipeline.add_component("ranker", ranker)

# Now, connect the components to each other
basic_rag_pipeline.connect("text_embedder.embedding", "retriever.query_embedding")
# basic_rag_pipeline.connect("retriever", "ranker")

🚅 Components
  - text_embedder: SentenceTransformersTextEmbedder
  - retriever: InMemoryEmbeddingRetriever
🛤️ Connections
  - text_embedder.embedding -> retriever.query_embedding (List[float])

In [32]:
# question = 'Могу ли я пить пиво на стриме?'

# basic_rag_pipeline.run({"text_embedder": {"text": question}, "ranker":{"query": question}})

Добавим словарь, по которому будем заменять англицизмы на действительно английские слова (т. к. в базе они хранятся именно на английском)

In [33]:
replace_dict = {
    'шортс': 'shorts',
    "рутуб": "rutube",
    "рутубе": "rutube",
    "рутуба": "rutube",
    "рутубу": "rutube",
    "ютуб": "youtube",
    "ютубе": "youtube",
    "ютуба": "youtube",
    "ютубу": "youtube",
    "смарт": "smart",
    "тв": "tv",
    "самсунг": "samsung",
    "урл": "url",
}

### Загрузим предварительно обученные модели для будущей классификации вопросов

In [34]:
!cp -r drive/MyDrive/HacksAI/Russia24/models/version_20240928_121531_train_0.80_test_0.66_valid_0.61/ model_1/
!cp -r drive/MyDrive/HacksAI/Russia24/models/version_20240928_123836_train_0.45_test_0.41_valid_0.32/ model_2/

In [35]:
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
import joblib

nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')

lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words('russian'))

loaded_models = {}
loaded_encoders = {}
loaded_vectorizers = {}

def preprocess(text):
    text = re.sub(r'\W+', ' ', text)

    words = nltk.word_tokenize(text)
    words = [lemmatizer.lemmatize(word) for word in words if word not in stop_words]

    return ' '.join(words)

def load_model_and_files(model_name, model_path, encoder_path, vectorizer_path):
    global loaded_models, loaded_encoders, loaded_vectorizers

    if model_name not in loaded_models:
        print(f"Загрузка модели {model_name}...")
        loaded_models[model_name] = joblib.load(model_path)
        loaded_encoders[model_name] = joblib.load(encoder_path)
        loaded_vectorizers[model_name] = joblib.load(vectorizer_path)
    else:
        print(f"Модель {model_name} уже загружена.")

def classify_question(
    question: str,
    model_name: str,
):
    global loaded_models, loaded_encoders, loaded_vectorizers

    preprocessed_question = preprocess(question)

    # Преобразование вопроса в TF-IDF вектор
    vectorizer = loaded_vectorizers[model_name]
    question_tfidf = vectorizer.transform([preprocessed_question])

    # Предсказание с помощью модели
    model = loaded_models[model_name]
    predicted_label_numeric = model.predict(question_tfidf)

    # Преобразование числовой метки обратно в текстовую метку
    encoder = loaded_encoders[model_name]
    predicted_label_text = encoder.inverse_transform(predicted_label_numeric)

    return predicted_label_text[0]

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [36]:
model_path_1 = "model_1/classifier_1.pkl"
encoder_path_1 = "model_1/label_encoder_1.pkl"
vectorizer_path_1 = "model_1/vectorizer_1.pkl"

model_path_2 = "model_2/classifier_2.pkl"
encoder_path_2 = "model_2/label_encoder_2.pkl"
vectorizer_path_2 = "model_2/vectorizer_2.pkl"

load_model_and_files('model_1', model_path_1, encoder_path_1, vectorizer_path_1)
load_model_and_files('model_2', model_path_2, encoder_path_2, vectorizer_path_2)

Загрузка модели model_1...
Загрузка модели model_2...


### Интерфейс для получения ответа из RAG пайплайна

In [37]:
import re
import time
import pymorphy2
import pandas as pd

def get_answer_from_rag(
    question: str,
    basic_rag_pipeline,
    threshold: float = 0.87,
    df:pd.DataFrame = final_df,
    ):
    start_time = time.time()

    morph = pymorphy2.MorphAnalyzer()

    question = question.lower()
    question = re.sub(r'[^\w\s-]', '', question)

    if replace_dict:
        words = question.split()

        replaced_words = []
        for word in words:
            parsed = morph.parse(word)
            if parsed:
                lemma = parsed[0].normal_form
            else:
                lemma = word
            replaced_word = replace_dict.get(lemma, word)
            replaced_words.append(replaced_word)

        question = ' '.join(replaced_words)

    print(f"Processed question: {question}")

    response = basic_rag_pipeline.run({"text_embedder": {"text": question}})
    print(response)

    document = response['retriever']['documents'][0]

    target_q = document.content
    score = document.score

    if score  < threshold:
      answer_text = "Ответ не найден."
      class_1 = classify_question(question, "model_1")
      class_2 = classify_question(question, "model_2")
    else:
      target_answer = df.loc[df['Вопрос'] == target_q].iloc[0]

      answer_text = target_answer['Ответ из БЗ']
      class_1 = target_answer['Классификатор 1 уровня']
      class_2 = target_answer['Классификатор 2 уровня']

    return answer_text, class_1, class_2

In [39]:
get_answer_from_rag(
    "Проверьте, что файл в подходящем формате, в видео весит не больше 25 ГБ Проверьте, что файл Проверьте, что файл  Проверьте, что файл Проверьте, что файл  Проверьте, что файл Проверьте, что файл",
    basic_rag_pipeline,
    threshold = 0.87)

Processed question: проверьте что файл в подходящем формате в видео весит не больше 25 гб проверьте что файл проверьте что файл проверьте что файл проверьте что файл проверьте что файл проверьте что файл


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

{'retriever': {'documents': [Document(id=f2bbb4bfc7430e70847252b10dd2e96ee94b10bf368585225c2db9f2f88a9cd1, content: 'Какой формат видео могу загрузить?', meta: {'idx': 1058}, score: 0.8545212309227049), Document(id=52866feaed98035dd48a407fa82b750bb0e25f027059414e708303e34746030c, content: 'Почнм нельзя смотреть видео в хорошем качестве?', meta: {'idx': 1010}, score: 0.853633732353968), Document(id=b28d282c669719fdfe0089881d47dfc45cdfda274b891021b23d01f5a12482de, content: 'не могу загрущить видео возникла ошибка', meta: {'idx': 1000}, score: 0.8530208061436719), Document(id=96c938bfa487cb47e7d2e30bed2e92d608dbb0c95af72d2ba3980b8248fa3c07, content: 'ошибка при загрузке видео', meta: {'idx': 1001}, score: 0.8528037257712519), Document(id=b55c34bea944dfd9877205cf17bbc5328622f660dd4efb5c975a6a0a937452a1, content: 'появляется ошибка перед тем как запустить видео', meta: {'idx': 1007}, score: 0.8522081078984958), Document(id=39193d5bd7767ddc4703d86bde0e0831f422ec577857f0eac5da7ea7d14da899, co

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


('Ответ не найден.', 'УПРАВЛЕНИЕ АККАУНТОМ', 'Персонализация')

In [ ]:
get_answer_from_rag(
    "Умпа лумпа",
    basic_rag_pipeline,
    threshold = 0.87)

Processed question: умпа лумпа


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

{'retriever': {'documents': [Document(id=78b41505183b1a0825b88c56c40fd3a6d5d55f827fdc9a52635a54cd11c25039, content: 'К какой категории относится мой клип', meta: {'idx': 1015}, score: 0.8180421245063306), Document(id=285c8746cf58cf3870e5634870d50f1512d4904c3e617985d12210af54837854, content: 'Какой логин указывать в студии на смартфоне? Забыла почта или номер нужен', meta: {'idx': 375}, score: 0.8167120211357835), Document(id=cdc4ea5f709b05846781373a7a3c8b1714b7c3cbc46ba5b4d6bd8fd2be2afc45, content: 'Какой логин указывать в студии на смартфоне? Вхожу первый раз на самсунге', meta: {'idx': 446}, score: 0.816563836633589), Document(id=cf807f98daa0d50b2e146db8123a90fb73734873e86858d9d4bc74481bd20770, content: 'я работаю в группе компаний, у кажой компании есть канал свой, их около 70. Они могут все дать мне л...', meta: {'idx': 527}, score: 0.8156264751434903), Document(id=2b2329404132b3fcc3a526d3a134946d96d7c4921589f27a9eb01bd34aa81e23, content: 'Не могу нати кнопки включения субтитров', 

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


('Ответ не найден.', 'УПРАВЛЕНИЕ АККАУНТОМ', 'Персонализация')

### Асинхронная функция для будущего использования с API

In [ ]:
import asyncio
from pydantic import BaseModel

class Answer(BaseModel):
    answer: str
    class_1: str
    class_2: str

async def get_answer(question: str, basic_rag_pipeline) -> Answer:
    """
    Асинхронная функция принимает вопрос, получает ответ и классы с помощью RAG pipeline
    и возвращает объект AnswerModel.

    Параметры:
    - question (str): Вопрос, который нужно обработать.
    - basic_rag_pipeline: RAG pipeline для обработки запроса.
    - replace_dict (dict, optional): Словарь для замены слов в вопросе.
    - df (pd.DataFrame, optional): DataFrame, содержащий столбцы 'Вопрос из БЗ', 'Ответ из БЗ',
                                    'Классификатор 1 уровня' и 'Классификатор 2 уровня'.

    Возвращает:
    - AnswerModel: Объект с полями answer, class_1 и class_2.
    """
    loop = asyncio.get_event_loop()
    answer_text, class_1, class_2 = await loop.run_in_executor(
        None,
        get_answer_from_rag,
        question,
        basic_rag_pipeline,
    )

    return Answer(
        answer=answer_text,
        class_1=class_1 if class_1 else "",
        class_2=class_2 if class_2 else "",
    )

In [ ]:
ttest = await get_answer("Умпа Лумпа?", basic_rag_pipeline)
print("-------------")
print(ttest)

Processed question: умпа лумпа


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

{'retriever': {'documents': [Document(id=78b41505183b1a0825b88c56c40fd3a6d5d55f827fdc9a52635a54cd11c25039, content: 'К какой категории относится мой клип', meta: {'idx': 1015}, score: 0.8180421245063306), Document(id=285c8746cf58cf3870e5634870d50f1512d4904c3e617985d12210af54837854, content: 'Какой логин указывать в студии на смартфоне? Забыла почта или номер нужен', meta: {'idx': 375}, score: 0.8167120211357835), Document(id=cdc4ea5f709b05846781373a7a3c8b1714b7c3cbc46ba5b4d6bd8fd2be2afc45, content: 'Какой логин указывать в студии на смартфоне? Вхожу первый раз на самсунге', meta: {'idx': 446}, score: 0.816563836633589), Document(id=cf807f98daa0d50b2e146db8123a90fb73734873e86858d9d4bc74481bd20770, content: 'я работаю в группе компаний, у кажой компании есть канал свой, их около 70. Они могут все дать мне л...', meta: {'idx': 527}, score: 0.8156264751434903), Document(id=2b2329404132b3fcc3a526d3a134946d96d7c4921589f27a9eb01bd34aa81e23, content: 'Не могу нати кнопки включения субтитров', 

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


### Тест модели

In [ ]:
import pandas as pd

def process_all_questions(input_file, question_col, basic_rag_pipeline, output_file):
    """
    Функция обрабатывает все вопросы из указанного файла, вызывает get_answer_from_rag для каждого,
    и сохраняет результаты в новый CSV файл.

    Параметры:
    - input_file: Путь к CSV или XLSX файлу с вопросами.
    - question_col: Название колонки, содержащей вопросы.
    - basic_rag_pipeline: RAG pipeline для обработки запроса.
    - output_file: Путь для сохранения результирующего CSV файла с вопросами и ответами.

    Возвращает:
    - DataFrame с исходными вопросами и найденными ответами.
    """

    file_extension = input_file.split('.')[-1].lower()

    # Чтение данных в зависимости от расширения
    if file_extension == 'csv':
        df_questions = pd.read_csv(input_file)
    elif file_extension == 'xlsx':
        df_questions = pd.read_excel(input_file)
    else:
        raise ValueError("Файл должен быть формата CSV или XLSX.")

    results = []

    for question in df_questions[question_col]:
        answer, class_1, class_2 = get_answer_from_rag(question, basic_rag_pipeline)
        results.append({'Вопрос': question, 'Ответ': answer})

    df_results = pd.DataFrame(results)
    df_results.to_csv(output_file, index=False, encoding='utf-8')

    print(f"Результаты сохранены в файл: {output_file}")
    return df_results

In [ ]:
main_path = "drive/MyDrive/HacksAI/Russia24/"

src_file_path = main_path + "ground_truth_data/gt_faq_and_cases_evaluation.xlsx"
out_file_path = main_path + "generated_data/pipeline4_answers.csv"

process_all_questions(src_file_path, 'Вопрос', basic_rag_pipeline, out_file_path)

Output hidden; open in https://colab.research.google.com to view.